Add fire lable(Link with FIRAMS data)


Setting environment

In [1]:


import numpy as np
import pandas as pd
from datetime import timedelta

import matplotlib.pyplot as plt
%matplotlib inline

Defining helper functions

In [2]:
#Check fire hotpots in area
def in_square(r_lat, r_lon, sq):
    return ((r_lat >=  sq[0]) & (r_lat <= sq[1]) & (r_lon >= sq[2]) & (r_lon <= sq[3]))

#Function for marking the square
def mark_square(r, dict_label_square):
    r_lat = r['latitude']
    r_lon = r['longitude']
    for label, square in dict_label_square.items():
        if in_square(r_lat, r_lon, square):
            return label
    
    return "not found"
#Read grid file
def parse_grid_file(grid_file: str):
    df = pd.read_csv(grid_file)
    vals = df.values
    str_to_arr = lambda s: np.array([float(x) for x in s.split(',')])
    vals = np.array([[str_to_arr(x2) for x2 in x1] for x1 in vals])
    return vals
#Dict for grid
def grid_to_dict(grid_csv):
    grid_arr = parse_grid_file(grid_csv)
    reshaped_grid = grid_arr.reshape(-1,8)
    grid_dict = {}
    for i in range(len(reshaped_grid)):
        lat_lon = np.sort(list(set(reshaped_grid[i])))
        grid_dict[i] = lat_lon
    
    return grid_dict
#Processing FIRAMS data
def viirs_pipe(viirs_csv, grid_csv):
    viirs = pd.read_csv(viirs_csv)
    viirs = viirs[['latitude', 'longitude', 'acq_date', 'acq_time']]
    grid_dict = grid_to_dict(grid_csv)
    viirs['region'] = viirs.apply(lambda r: mark_square(r, grid_dict), axis=1)
#     viirs['match_date'] = pd.to_datetime(small_clean_viirs_2019['acq_time']) - timedelta(n_days)
    return viirs
#Processing RS data
def img_pipe(img_csv, n_weeks = 5, n_day_range = 7):
    img = pd.read_csv(img_csv)
    img['date'] = pd.to_datetime(img['date'])   
    img['fire_start'] = img['date'] + timedelta(n_weeks*7)
    img['fire_end'] = img['date'] + timedelta(n_weeks*7+n_day_range)
    return img
#Add number of fires in the area
memory_dict = {}
def custom_merge(row, vrs):
    
    unique_event = (row['fire_start'], row['fire_end'],row['rect_id'])

    if unique_event not in memory_dict:
        events = (vrs[(vrs['acq_date']>= row['fire_start']) & 
                      (vrs['acq_date']<= row['fire_end']) & 
                      (vrs['region'] == row['rect_id'])])
        num_fires = len(events)
        memory_dict[unique_event] = num_fires
        print(num_fires)
    else:
        num_fires = memory_dict[unique_event]
        
    
    return num_fires

Processing FIRAMS data

Link all FIRAMS data

In [4]:
vrs = viirs_pipe("2021_Australia.csv", 'grid.csv')
vrs['acq_date'] = pd.to_datetime(vrs['acq_date'])


In [5]:
viirs_2016 = viirs_pipe("2016_Australia.csv", 'grid.csv')


In [6]:
viirs_2017 = viirs_pipe("2017_Australia.csv", 'grid.csv')


In [7]:
viirs_2018 = viirs_pipe("2018_Australia.csv", 'grid.csv')


In [8]:
viirs_2019 = viirs_pipe("2019_Australia.csv", 'grid.csv')


In [9]:
viirs_2020 = viirs_pipe("2020_Australia.csv", 'grid.csv')


C:\Users\32429\AppData\Local\Temp\ipykernel_15428\1636953743.py:33: DtypeWarning: Columns (13) have mixed types. Specify dtype option on import or set low_memory=False.
  viirs = pd.read_csv(viirs_csv)


In [10]:
viirs_2021 = vrs


In [11]:
viirs = pd.concat([viirs_2016,viirs_2017, viirs_2018, viirs_2019,viirs_2020,viirs_2021], axis=0)
len(viirs)

5464602

In [12]:

viirs

latitude   longitude             acq_date  acq_time     region
0      -33.791821  150.887192             2016/1/1       313  not found
1      -31.369591  151.528259             2016/1/1       314  not found
2      -31.910295  152.458817             2016/1/1       314  not found
3      -27.245190  152.284760             2016/1/1       315  not found
4      -27.518364  149.384384             2016/1/1       315  not found
...           ...         ...                  ...       ...        ...
795910 -37.171188  141.188217  2021-12-31 00:00:00      1630  not found
795911 -37.183067  141.186295  2021-12-31 00:00:00      1630  not found
795912 -37.177052  141.168839  2021-12-31 00:00:00      1630  not found
795913 -28.962427  127.768417  2021-12-31 00:00:00      1630  not found
795914 -37.156525  141.162140  2021-12-31 00:00:00      1630  not found

[5464602 rows x 5 columns]

Select all FIRAMS data in study area

In [13]:
viirs = viirs[viirs['region'] != "not found"]
len(viirs)

67159

In [14]:
viirs.to_csv('clean-viirs.csv')
viirs['acq_date'] = pd.to_datetime(viirs['acq_date'])
viirs

C:\Users\32429\AppData\Local\Temp\ipykernel_15428\3699732965.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  viirs['acq_date'] = pd.to_datetime(viirs['acq_date'])


latitude   longitude   acq_date  acq_time region
67579  -11.445399  130.502686 2016-03-28       428   1947
67658  -11.444934  130.502655 2016-03-28      1715   1947
68501  -11.443841  130.501953 2016-03-29      1656   1946
68502  -11.469357  130.508896 2016-03-29      1656   2009
70286  -11.444445  130.502792 2016-03-30      1637   1946
...           ...         ...        ...       ...    ...
736000 -11.862935  130.950272 2021-12-05       506   4584
736001 -11.863754  130.945374 2021-12-05       506   4516
737433 -11.887119  130.937790 2021-12-06       442   4453
737440 -11.889159  130.938858 2021-12-06       442   4519
737445 -11.891958  130.942917 2021-12-06       442   4519

[67159 rows x 5 columns]

Add Fire Hotpots labels(has fire) from FIRAMS data to Landsat 8 RS image data

In [15]:
img_1 =img_pipe("index.csv", n_weeks = 5, n_day_range = 7)
min(img_1['date'])


Timestamp('2017-01-01 00:00:00')

In [16]:
img_1['fire_counts'] = img_1.apply(lambda r: custom_merge(r, viirs), axis = 1)
img_1.drop(['fire_start', 'fire_end'], axis = 1).to_csv('img_with_labels.csv', index = False)

0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
4
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


In [17]:
img_1.describe()

rect_id                           date       Aerosol   
count  635554.000000                         635554  6.355540e+05  \
mean     4034.787411  2019-07-23 18:54:25.316243456  2.482981e-02   
min         0.000000            2017-01-01 00:00:00  2.616496e-07   
25%      2034.250000            2018-06-04 00:00:00  1.638823e-02   
50%      4074.000000            2019-08-10 00:00:00  2.264192e-02   
75%      6067.000000            2020-08-28 00:00:00  3.051715e-02   
max      7687.000000            2021-12-30 00:00:00  1.128319e+00   
std      2298.372047                            NaN  1.873275e-02   

                Blue          Green            Red            NIR   
count  635554.000000  635554.000000  635554.000000  635554.000000  \
mean        0.032583       0.058214       0.057607       0.238980   
min         0.000035       0.000255       0.000728       0.001149   
25%         0.023871       0.046992       0.043480       0.213533   
50%         0.030193       0.054439       0.054550       0.243303   
75%         0.037872       0.065028       0.067646       0.265935   
max         1.123190       1.075049       1.088018       1.099837   
std         0.019086       0.021235       0.024275       0.045958   

               SWIR1          SWIR2    Temperature  ...           NDVI   
count  635554.000000  635554.000000  635554.000000  ...  635554.000000  \
mean        0.166434       0.089543      32.987489  ...       0.613514   
min         0.001030       0.001140       0.001963  ...      -0.866926   
25%         0.137954       0.066757      29.737324  ...       0.547888   
50%         0.166761       0.085240      33.775926  ...       0.626439   
75%         0.197830       0.110818      38.221236  ...       0.696964   
max         0.630115       1.599985      62.043486  ...       0.988864   
std         0.051132       0.034883       8.555161  ...       0.114384   

               GNDVI           NDMI           SAVI          MSAVI   
count  635554.000000  635554.000000  635554.000000  635554.000000  \
mean        0.607284       0.191913       0.382427       0.811332   
min        -0.972269      -0.912490      -0.259712       0.343227   
25%         0.570251       0.087825       0.337978       0.765098   
50%         0.624339       0.193706       0.390966       0.816632   
75%         0.671598       0.282842       0.438610       0.864324   
max         0.998004       0.869944       0.563845       0.999985   
std         0.097217       0.141367       0.078850       0.076519   

             CIGreen            NBR                     fire_start   
count  635554.000000  635554.000000                         635554  \
mean        3.343744       0.191913  2019-08-27 18:54:25.316243456   
min        -0.985940      -0.912490            2017-02-05 00:00:00   
25%         2.653877       0.087825            2018-07-09 00:00:00   
50%         3.323954       0.193706            2019-09-14 00:00:00   
75%         4.090095       0.282842            2020-10-02 00:00:00   
max      1000.029412       0.869944            2022-02-03 00:00:00   
std         1.730860       0.141367                            NaN   

                            fire_end    fire_counts  
count                         635554  635554.000000  
mean   2019-09-03 18:54:25.316243456       0.040093  
min              2017-02-12 00:00:00       0.000000  
25%              2018-07-16 00:00:00       0.000000  
50%              2019-09-21 00:00:00       0.000000  
75%              2020-10-09 00:00:00       0.000000  
max              2022-02-10 00:00:00      27.000000  
std                              NaN       0.422256  

[8 rows x 21 columns]